In [10]:
import bitarray
import math
import sys

import numpy as np
import scipy.io.wavfile as wav

from IPython.display import Audio

np.set_printoptions(threshold=sys.maxsize)

In [11]:
def phase_enc(signal, text, L = 1024):
  plain = signal[:,0]
  data = bitarray.bitarray()
  data.frombytes(text.encode('ascii'))
  I = len(plain)
  m = len(data)
  N = math.floor(I / L)

  s = np.reshape(plain[: N * L], (L, N))

  w = np.fft.fft(s)
  Phi = np.angle(w)
  A = np.abs(w)

  print(Phi)

  DeltaPhi = np.zeros((L, N))
  for k in range(1, N):
    DeltaPhi[:, k] = Phi[:, k] - Phi[:, k - 1]

  PhiData = np.zeros((1, m))
  for k in range(m):
    PhiData[0][k] = np.pi / 2 if data[k] == 0 else -np.pi / 2

  Phi_new = Phi.copy()
  Phi_new[L // 2 - m : L // 2, 0] = PhiData
  Phi_new[L // 2 : L // 2 + m, 0] = -np.flip(PhiData)

  for k in range(1, N):
    Phi_new[:, k] = Phi_new[:, k - 1] + DeltaPhi[:, k]

  z = np.real(np.fft.ifft(np.multiply(A, np.exp(1j * Phi_new))))
  snew = np.reshape(z,(N * L))
  out = np.concatenate((snew, plain[N * L:]), axis=0)
  out = np.vstack(out)
  right = np.vstack(signal[:,1])
  out = np.concatenate((out, right), axis=1)
  return np.asarray(out, dtype=np.int16)



In [12]:
fs, x = wav.read('sample.wav')
print(f'Sample rate is {fs} Gz')
print(f'File contains {x.shape[0]} samples')
print(f'Approximate audio duration is {x.shape[0] / fs} s')
Audio('sample.wav')

Sample rate is 44100 Gz
File contains 140928 samples
Approximate audio duration is 3.1956462585034013 s


In [13]:

xmod = phase_enc(x, 'Do Androids Dream of Electric Sheep?')

wav.write('sample-mod.wav', fs, xmod)
Audio('sample-mod.wav')

[[ 3.14159265e+00 -1.52019601e+00 -1.25737994e+00 -1.58423868e+00
  -9.50333109e-01 -1.94198595e+00 -1.56456516e+00 -1.08028415e+00
  -1.53467408e+00 -1.59065165e+00 -1.33150069e+00 -2.16275705e+00
  -1.93117809e+00  1.55764042e+00 -1.22075175e+00 -2.42951969e+00
   1.17320838e-01 -2.05644365e-01 -1.65392093e+00 -9.40677066e-01
  -1.08754054e+00 -1.75205700e+00 -1.90602652e+00 -2.66314559e+00
  -5.85983157e-01 -2.83685654e-01 -2.22451507e+00 -6.09696786e-01
  -1.93597248e+00 -1.39154484e+00 -9.33647571e-01 -2.72148336e-01
   6.81758687e-01  2.28332164e-01 -2.98374452e-01 -6.35883787e-01
  -1.26680103e-02  4.23015941e-01 -1.06174066e+00  2.34007594e-01
  -6.57297772e-01 -7.10447635e-01  1.04632873e+00 -2.23343359e+00
   1.54563265e-01  1.19812457e+00 -3.27080905e-02 -2.88087531e-01
  -9.24174842e-01 -9.93019288e-01 -2.26339222e-01  4.09909994e-01
   1.70972948e-01 -2.27522665e-01 -6.72012312e-01  1.88304262e-01
  -1.91617035e-01 -3.54818859e-01 -6.52638669e-01 -1.59530980e-01
  -8.46055